In [38]:
%load_ext autoreload
%autoreload 2
import pandas as pd
import numpy as np
import pandana as pdna
from pandana.loaders import osm
%matplotlib inline
from mpl_toolkits.basemap import Basemap
from pandana.loaders import osm
import geopandas as gpd

import warnings
warnings.filterwarnings('ignore')
from bokeh.models import BoxZoomTool
from bokeh.plotting import figure, output_notebook, show


The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [37]:
# from bokeh.plotting import figure, show, output_file
# from bokeh.tile_providers import CARTODBPOSITRON

# # output_file("tile.html")

# # range bounds supplied in web mercator coordinates
# p = figure(x_range=(-2000000, 6000000), y_range=(-1000000, 7000000),
#            x_axis_type="mercator", y_axis_type="mercator")
# p.add_tile(CARTODBPOSITRON)



In [10]:
beam_network_nodes = pd.read_csv('beam-network-nodes.csv')
beam_network_nodes.head()

id              x             y         lon        lat
0     0  556999.874645  4.160239e+06 -122.354382  37.587447
1     1  556694.020184  4.160335e+06 -122.357839  37.588328
2    10  524783.388304  4.251499e+06 -122.716128  38.411391
3   100  580390.236693  4.173055e+06 -122.088063  37.701202
4  1000  579889.102807  4.139979e+06 -122.097350  37.403148

In [11]:
access_2010 = pd.read_csv('indicators_output/access_10000_2010_node.csv') #jobs accessibilities by node within 10000m in 2010
access_2010_xy = access_2010.merge(beam_network_nodes, left_index=True, right_index=True)
access_2010_xy.head()
# access_2025 = pd.read_csv('indicators_output/access_10000_2010_census_tract.csv') #jobs accessibilities by node within 10000m in 2010
# access_2025.head()



Unnamed: 0  node_access_nhw  node_access_nhb  node_access_nha  \
0           8         0.000000              0.0         0.000000   
1          55         0.000000              0.0         0.000000   
2          56         0.000000              0.0         0.000000   
3          57    640603.589849              0.0         0.000000   
4          58    384622.648075              0.0    128207.549358   

   node_access_h    id              x             y         lon        lat  
0  518872.334314     0  556999.874645  4.160239e+06 -122.354382  37.587447  
1       0.000000     1  556694.020184  4.160335e+06 -122.357839  37.588328  
2  645352.677324    10  524783.388304  4.251499e+06 -122.716128  38.411391  
3       0.000000   100  580390.236693  4.173055e+06 -122.088063  37.701202  
4  128207.549358  1000  579889.102807  4.139979e+06 -122.097350  37.403148

In [34]:
lon_min = min(access_2010_xy['lon'])
lon_max = max(access_2010_xy['lon'])
lat_min = min(access_2010_xy['lat'])
lat_max = max(access_2010_xy['lat'])

print(lon_min, lon_max, lat_min, lat_max)
output_notebook()
BAY_AREA = x_range, y_range = ((lon_min,lon_max), (lat_min,lat_max)) #((lon_min,lon_max), (lat_min,lat_max))
plot_width  = int(750)
plot_height = int(plot_width//1.2)

def base_plot(tools='pan,wheel_zoom,reset',plot_width=plot_width, plot_height=plot_height, **plot_args):
    p = figure(tools=tools, plot_width=plot_width, plot_height=plot_height,
        x_range=x_range, y_range=y_range, outline_line_color=None,
        min_border=0, min_border_left=0, min_border_right=0,
        min_border_top=0, min_border_bottom=0, **plot_args)

    p.axis.visible = False
    p.xgrid.grid_line_color = None
    p.ygrid.grid_line_color = None

    p.add_tools(BoxZoomTool(match_aspect=True))

    return p

options = dict(line_color=None, fill_color='blue', size=5)

-123.530832 -121.20936399999701 36.8967310009079 38.8638110009245


Loading BokehJS ...

In [41]:
import datashader as ds
from datashader.bokeh_ext import InteractiveImage
from functools import partial
from datashader.utils import export_image
from datashader.colors import colormap_select, Greys9, Hot, inferno
from datashader import transfer_functions as tf
from bokeh.tile_providers import CARTODBPOSITRON


lon_min = min(access_2010_xy['lon'])
lon_max = max(access_2010_xy['lon'])
lat_min = min(access_2010_xy['lat'])
lat_max = max(access_2010_xy['lat'])

print(lon_min,lon_max,lat_min,lat_max)
plot_width  = int(750)
plot_height = int(plot_width//1.2)
BAY_AREA = x_range, y_range = ((lon_min,lon_max), (lat_min,lat_max)) #((lon_min,lon_max), (lat_min,lat_max))

# backgound = "black"
export = partial(export_image, export_path="indicators_output/", background="black")
# cm = partial(colormap_select, reverse=(background=="black"))

def create_image(x_range, y_range, w=plot_width, h=plot_height):
    cvs = ds.Canvas(plot_width=w, plot_height=h, x_range=x_range_wm, y_range=y_range_wm)
    agg = cvs.points(access_2010_xy, 'x', 'y', ds.sum('node_access_nha'))
    img = tf.shade(agg, cmap=inferno, how='eq_hist')
    return tf.dynspread(img, threshold=0.5, max_px=4)

              
p = figure(x_range=x_range, y_range=y_range,
           x_axis_type="mercator", y_axis_type="mercator")

p.add_tile(CARTODBPOSITRON)
export(create_image(*BAY_AREA),"BAY_nha")
InteractiveImage(p, create_image)

# show(p)

-123.530832 -121.20936399999701 36.8967310009079 38.8638110009245


In [36]:
import datashader as ds
from datashader.bokeh_ext import InteractiveImage
from functools import partial
from datashader.utils import export_image
from datashader.colors import colormap_select, Greys9, Hot, inferno
from datashader import transfer_functions as tf
from bokeh.tile_providers import CARTODBPOSITRON


x_min = min(access_2010_xy['x'])
x_max = max(access_2010_xy['x'])
y_min = min(access_2010_xy['y'])
y_max = max(access_2010_xy['y'])

print(x_min,x_max,y_min,y_max)
plot_width  = int(750)
plot_height = int(plot_width//1.2)
BAY_AREA_wm = x_range_wm, y_range_wm = ((x_min,x_max), (y_min,y_max)) #((lon_min,lon_max), (lat_min,lat_max))

# backgound = "black"
export = partial(export_image, export_path="indicators_output/", background="black")
# cm = partial(colormap_select, reverse=(background=="black"))

def create_image(x_range_wm, y_range_wm, w=plot_width, h=plot_height):
    cvs = ds.Canvas(plot_width=w, plot_height=h, x_range=x_range_wm, y_range=y_range_wm)
    agg = cvs.points(access_2010_xy, 'x', 'y', ds.sum('node_access_nha'))
    img = tf.shade(agg, cmap=inferno, how='eq_hist')
    return tf.dynspread(img, threshold=0.5, max_px=4)

              
p = figure(x_range=x_range_wm, y_range=y_range_wm)
#            x_axis_type="mercator", y_axis_type="mercator")

p.add_tile(CARTODBPOSITRON)
export(create_image(*BAY_AREA_wm),"BAY_nha")
InteractiveImage(p, create_image)

# show(p)

453884.968000266 659195.504800888 4084388.84894474 4301827.68787273


In [26]:
import numpy as np
from functools import partial

def create_image90(x_range, y_range, w=plot_width, h=plot_height):
    cvs = ds.Canvas(plot_width=w, plot_height=h, x_range=x_range, y_range=y_range)
    agg = cvs.points(access_2010_xy, 'lon', 'lat',  ds.count('node_access_nha'))
    img = tf.shade(agg.where(agg>np.percentile(agg,90)), cmap=inferno, how='eq_hist')
    return tf.dynspread(img, threshold=0.3, max_px=4)

p = base_plot()
p.add_tile(CARTODBPOSITRON)
export(create_image(x_range_wm, y_range_wm),"NYCT_90th")
InteractiveImage(p, create_image90)

In [4]:
beam_network_links = pd.read_csv('beam-network-links.csv')
beam_network_nodes = pd.read_csv('beam-network-nodes.csv')

In [5]:
net=pdna.Network(beam_network_nodes.x, beam_network_nodes.y, beam_network_links["from"], beam_network_links["to"],
                 beam_network_links[["travelTime"]])
net.precompute(10000)

